In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['公司代號'] != '公司代號']
    df = df[~df['公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[['公司代號','公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[['公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on='公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_revenue_sii = generate_df_for_stocktype(107, 2, 3, 'sii', 'Revenue', '營業收入', '綜合損益彙總表')

df_revenue_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業收入
year: 107
season: 1
營業收入
year: 106
season: 4
營業收入
year: 106
season: 3
營業收入
year: 106
season: 2
營業收入
year: 106
season: 1
營業收入
year: 105
season: 4
營業收入
year: 105
season: 3
營業收入
year: 105
season: 2
營業收入
year: 105
season: 1
營業收入
year: 104
season: 4
營業收入
year: 104
season: 3
營業收入
year: 104
season: 2


公司代號     公司名稱 Revenue(%)_107Q2 Revenue(%)_107Q1 Revenue(%)_106Q4  \
0    2809     京城銀行              NaN              NaN              NaN   
1    1101       台泥         57500246         24179214         98311776   
2    1102       亞泥         39009089         16573882         64899248   
3    1103       嘉泥          1000927           471257          2095607   
4    1104     環球水泥          2314855          1166097          4405376   
5    1108     幸福水泥          1684246           832706          3434454   
6    1109     信大水泥          2809557          1061381          5375877   
7    1110       東泥           792194           412490          1716725   
8    1201     味全公司          8828716          3917347         17749330   
9    1203     味王公司          2946087          1447466          6195171   
10   1210     大成長城         34984170         17123119         75931014   
11   1213       大飲           292227           149094           649522   
12   1215     卜蜂企業         10220457          4957240         19865000   
13   1216       統一        214645776        104288097        399860953   
14   1217      愛之味          1982512          1028433          4146490   
15   1218     泰山企業          3846852          1844853          7681801   
16   1219     福壽實業          5850333          2880708         10822788   
17   1220       台榮          1203975           573904          2366605   
18   1225      福懋油          5463107          2794671         10757313   
19   1227       佳格         12421997          7414473         26477924   
20   1229     聯華實業          2488302          1224453          4845301   
21   1231     聯華食品          3767881          2016950          7031023   
22   1232      大統益          8382090          4117718         16884341   
23   1233       天仁          1086757           553440          2130351   
24   1234       黑松          4454176          2316158          9090115   
25   1235       興泰            13381             6033            76878   
26   1236     宏亞食品           898907           571543          1878973   
27   1256  鮮活果汁-KY          1634338           699961          2917183   
28   1262    綠悅-KY          2137649          1276116          6296238   
29   1301       台塑        116643451         54167368        206709755   
30   1303     南亞塑膠        168674081         82219991        306139952   
31   1304       台聚         30332479         14670146         58133943   
32   1305       華夏          7822558          4144200         14701741   
33   1307     三芳化工          4457733          2385362          9855355   
34   1308       亞聚          2961396          1326214          6404467   
35   1309     台達化工         10788137          4842167         19821042   
36   1310       台苯          8076162          4004442         14750826   
37   1312     國喬石化         12291297          6386708         23350965   
38   1313       聯成         30044450         13569504         50600125   
39   1314      中石化         18942433          9494452         33335970   
40   1315     達新工業          1175379           573452          2654707   
41   1316       上曜          1184595           766579          2159740   
42   1319       東陽         12051478          6245138         24452883   
43   1321       大洋          2447215          1190142          4467046   
44   1323       永裕          1809540           825302          3241637   
45   1324     地球工業           567590           261060          1227153   
46   1325       恒大           447137           229124           865210   
47   1326       台化        198653498         98956552        358421471   
48   1337    再生-KY           716771           343807          4588271   
49   1338    廣華-KY          4036378          1987165          7967359   
50   1339       昭輝          1431877           722810          2837280   
51   1340    勝悅-KY          1239618           490794          3406504   
52   1402      遠東新        105396469         51457884        217846948   
53   1410       南染           265883           122940           

In [5]:
df_revenue_otc = generate_df_for_stocktype(107, 2, 3, 'otc', 'Revenue', '營業收入', '綜合損益彙總表')

df_revenue_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業收入
year: 107
season: 1
營業收入
year: 106
season: 4
營業收入
year: 106
season: 3
營業收入
year: 106
season: 2
營業收入
year: 106
season: 1
營業收入
year: 105
season: 4
營業收入
year: 105
season: 3
營業收入
year: 105
season: 2
營業收入
year: 105
season: 1
營業收入
year: 104
season: 4
營業收入
year: 104
season: 3
營業收入
year: 104
season: 2


公司代號    公司名稱 Revenue(%)_107Q2 Revenue(%)_107Q1 Revenue(%)_106Q4  \
0    6026    福邦證券              NaN              NaN              NaN   
1    1258   其祥-KY          1409658           677719          2480922   
2    1259      安心          2543588          1235482          4919312   
3    1264      德麥          1918781           959944          3675034   
4    1333     恩得利           204505           102652           418555   
5    1336      台翰          1269314           602809          2284494   
6    1565    精華光學          3305585          1583200          6417887   
7    1566      捷邦          2652481          1289891          5311419   
8    1569      濱川          1638868           785233          3591565   
9    1570    力肯實業           303879           135472           806650   
10   1580    新麥企業          2012693           854051          4614233   
11   1584    精剛精密           326104           191201           955679   
12   1586    和勤精機          1253630           602633          2223818   
13   1591   駿吉-KY           357829           155749           416161   
14   1593      祺驊           332117           155868           834492   
15   1595    川寶科技           924822           427347          1369985   
16   1597      直得          1089719           504842          1488259   
17   1599     宏佳騰           974250           355607          2430420   
18   1742      台蠟           195230            93607           418837   
19   1752      南光           769117           378872          1503720   
20   1777      生泰           395839           191471           694985   
21   1781    合世生醫           305627            89031           534459   
22   1784    訊聯生技           376298           186970           697401   
23   1785     光洋科         10219933          5126362         15753593   
24   1787     福盈科           957092           451956          1846505   
25   1788    杏昌生技          1537640           771056          2958880   
26   1795    美時製藥          3125066          1489784          6423760   
27   1799      易威           175954            92196           374478   
28   1813     寶利徠           214896           113054           397829   
29   1815    富喬工業          2378008          1157824          4812201   
30   2035    唐榮公司          8603295          4239350         18918149   
31   2061      風青           728234           352293          1268422   
32   2063      世鎧           520033           242420           947205   
33   2064      晉椿          1368923           687600          2447737   
34   2066      世德           655138           313605          1337000   
35   2067      嘉鋼           716616           342077          1259332   
36   2221    大甲永和           538555           262646           937086   
37   2230      泰茂           274476           129601           551138   
38   2233      宇隆          1341929           676108          2389410   
39   2235      謚源           361023           181239           812066   
40   2596    綠意開發          1119772           561467          1220023   
41   2640     大車隊           944412           463421          1694837   
42   2641    正德海運           374353           163636           740251   
43   2643      捷迅          1290706           621118          2661664   
44   2718      晶悅           101419            54810           221892   
45   2719     燦星旅          1194742           483175          2437341   
46   2724   富驛-KY           329202           147696           757162   
47   2726   雅茗-KY          1057703           525688          1994450   
48   2729    瓦城泰統          2125661          1069887          4106715   
49   2732    六角國際          1722650           793867          2497946   
50   2734     易飛網           510346           249918          1231107   
51   2736      高野           293643           154753           649848   
52   2740      天蔥           202678           110086           588698   
53   2916    滿心企業           631202           333083          1297233   
54   2924   東凌-KY           347095           

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_revenue = pd.concat([df_revenue_sii,df_revenue_otc],axis=0, ignore_index=True)

df_revenue

公司代號     公司名稱 Revenue(%)_107Q2 Revenue(%)_107Q1 Revenue(%)_106Q4  \
0     2809     京城銀行              NaN              NaN              NaN   
1     1101       台泥         57500246         24179214         98311776   
2     1102       亞泥         39009089         16573882         64899248   
3     1103       嘉泥          1000927           471257          2095607   
4     1104     環球水泥          2314855          1166097          4405376   
5     1108     幸福水泥          1684246           832706          3434454   
6     1109     信大水泥          2809557          1061381          5375877   
7     1110       東泥           792194           412490          1716725   
8     1201     味全公司          8828716          3917347         17749330   
9     1203     味王公司          2946087          1447466          6195171   
10    1210     大成長城         34984170         17123119         75931014   
11    1213       大飲           292227           149094           649522   
12    1215     卜蜂企業         10220457          4957240         19865000   
13    1216       統一        214645776        104288097        399860953   
14    1217      愛之味          1982512          1028433          4146490   
15    1218     泰山企業          3846852          1844853          7681801   
16    1219     福壽實業          5850333          2880708         10822788   
17    1220       台榮          1203975           573904          2366605   
18    1225      福懋油          5463107          2794671         10757313   
19    1227       佳格         12421997          7414473         26477924   
20    1229     聯華實業          2488302          1224453          4845301   
21    1231     聯華食品          3767881          2016950          7031023   
22    1232      大統益          8382090          4117718         16884341   
23    1233       天仁          1086757           553440          2130351   
24    1234       黑松          4454176          2316158          9090115   
25    1235       興泰            13381             6033            76878   
26    1236     宏亞食品           898907           571543          1878973   
27    1256  鮮活果汁-KY          1634338           699961          2917183   
28    1262    綠悅-KY          2137649          1276116          6296238   
29    1301       台塑        116643451         54167368        206709755   
30    1303     南亞塑膠        168674081         82219991        306139952   
31    1304       台聚         30332479         14670146         58133943   
32    1305       華夏          7822558          4144200         14701741   
33    1307     三芳化工          4457733          2385362          9855355   
34    1308       亞聚          2961396          1326214          6404467   
35    1309     台達化工         10788137          4842167         19821042   
36    1310       台苯          8076162          4004442         14750826   
37    1312     國喬石化         12291297          6386708         23350965   
38    1313       聯成         30044450         13569504         50600125   
39    1314      中石化         18942433          9494452         33335970   
40    1315     達新工業          1175379           573452          2654707   
41    1316       上曜          1184595           766579          2159740   
42    1319       東陽         12051478          6245138         24452883   
43    1321       大洋          2447215          1190142          4467046   
44    1323       永裕          1809540           825302          3241637   
45    1324     地球工業           567590           261060          1227153   
46    1325       恒大           447137           229124           865210   
47    1326       台化        198653498         98956552        358421471   
48    1337    再生-KY           716771           343807          4588271   
49    1338    廣華-KY          4036378          1987165          7967359   
50    1339       昭輝          1431877           722810          2837280   
51    1340    勝悅-KY          1239618           490794          3406504   
52    1402      遠東新        105396469         51457884        217846948   
53    1410

In [7]:
#檢查column資料型態

#df_revenue.info() #non-null object
#df_revenue.dtypes #object
#df_revenue.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
Revenue(%)_107Q1    float64
Revenue(%)_106Q4    float64
Revenue(%)_106Q3    float64
Revenue(%)_106Q2    float64
Revenue(%)_106Q1    float64
Revenue(%)_105Q4    float64
Revenue(%)_105Q3    float64
Revenue(%)_105Q2    float64
Revenue(%)_105Q1    float64
Revenue(%)_104Q4    float64
Revenue(%)_104Q3    float64
Revenue(%)_104Q2    float64
Revenue(%)_104Q1    float64
dtype: object
'''

df_revenue = df_revenue.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_revenue.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                  int64
公司名稱                 object
Revenue(%)_107Q2    float64
Revenue(%)_107Q1    float64
Revenue(%)_106Q4    float64
Revenue(%)_106Q3    float64
Revenue(%)_106Q2    float64
Revenue(%)_106Q1    float64
Revenue(%)_105Q4    float64
Revenue(%)_105Q3    float64
Revenue(%)_105Q2    float64
Revenue(%)_105Q1    float64
Revenue(%)_104Q4    float64
Revenue(%)_104Q3    float64
Revenue(%)_104Q2    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['Revenue(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['Revenue(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['Revenue(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['Revenue(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_revenue['Growth_{0}Q{1}'.format(year, season)] = df_revenue.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_revenue['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_revenue.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [14]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['有價證券代號及名稱'] != '股票']
    df = df[~df['有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df['產業別'] > '0']
    del newdf['國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf['備註']

    df2=newdf['有價證券代號及名稱'].str.split(' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if '　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split('　')[1]
            df2.iat[i,0]=df2.iat[i,0].split('　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:'公司代號',1:'股票名稱'})
    del newdf['有價證券代號及名稱']

    return newdf

In [15]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_revenue = df_revenue.merge(df_basicinfo, on='公司代號', how='inner')

df_revenue

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  Revenue(%)_107Q2  Revenue(%)_107Q1  Revenue(%)_106Q4  \
0     2809     京城銀行               NaN               NaN               NaN   
1     1101       台泥      5.750025e+07      2.417921e+07      9.831178e+07   
2     1102       亞泥      3.900909e+07      1.657388e+07      6.489925e+07   
3     1103       嘉泥      1.000927e+06      4.712570e+05      2.095607e+06   
4     1104     環球水泥      2.314855e+06      1.166097e+06      4.405376e+06   
5     1108     幸福水泥      1.684246e+06      8.327060e+05      3.434454e+06   
6     1109     信大水泥      2.809557e+06      1.061381e+06      5.375877e+06   
7     1110       東泥      7.921940e+05      4.124900e+05      1.716725e+06   
8     1201     味全公司      8.828716e+06      3.917347e+06      1.774933e+07   
9     1203     味王公司      2.946087e+06      1.447466e+06      6.195171e+06   
10    1210     大成長城      3.498417e+07      1.712312e+07      7.593101e+07   
11    1213       大飲      2.922270e+05      1.490940e+05      6.495220e+05   
12    1215     卜蜂企業      1.022046e+07      4.957240e+06      1.986500e+07   
13    1216       統一      2.146458e+08      1.042881e+08      3.998610e+08   
14    1217      愛之味      1.982512e+06      1.028433e+06      4.146490e+06   
15    1218     泰山企業      3.846852e+06      1.844853e+06      7.681801e+06   
16    1219     福壽實業      5.850333e+06      2.880708e+06      1.082279e+07   
17    1220       台榮      1.203975e+06      5.739040e+05      2.366605e+06   
18    1225      福懋油      5.463107e+06      2.794671e+06      1.075731e+07   
19    1227       佳格      1.242200e+07      7.414473e+06      2.647792e+07   
20    1229     聯華實業      2.488302e+06      1.224453e+06      4.845301e+06   
21    1231     聯華食品      3.767881e+06      2.016950e+06      7.031023e+06   
22    1232      大統益      8.382090e+06      4.117718e+06      1.688434e+07   
23    1233       天仁      1.086757e+06      5.534400e+05      2.130351e+06   
24    1234       黑松      4.454176e+06      2.316158e+06      9.090115e+06   
25    1235       興泰      1.338100e+04      6.033000e+03      7.687800e+04   
26    1236     宏亞食品      8.989070e+05      5.715430e+05      1.878973e+06   
27    1256  鮮活果汁-KY      1.634338e+06      6.999610e+05      2.917183e+06   
28    1262    綠悅-KY      2.137649e+06      1.276116e+06      6.296238e+06   
29    1301       台塑      1.166435e+08      5.416737e+07      2.067098e+08   
30    1303     南亞塑膠      1.686741e+08      8.221999e+07      3.061400e+08   
31    1304       台聚      3.033248e+07      1.467015e+07      5.813394e+07   
32    1305       華夏      7.822558e+06      4.144200e+06      1.470174e+07   
33    1307     三芳化工      4.457733e+06      2.385362e+06      9.855355e+06   
34    1308       亞聚      2.961396e+06      1.326214e+06      6.404467e+06   
35    1309     台達化工      1.078814e+07      4.842167e+06      1.982104e+07   
36    1310       台苯      8.076162e+06      4.004442e+06      1.475083e+07   
37    1312     國喬石化      1.229130e+07      6.386708e+06      2.335096e+07   
38    1313       聯成      3.004445e+07      1.356950e+07      5.060012e+07   
39    1314      中石化      1.894243e+07      9.494452e+06      3.333597e+07   
40    1315     達新工業      1.175379e+06      5.734520e+05      2.654707e+06   
41    1316       上曜      1.184595e+06      7.665790e+05      2.159740e+06   
42    1319       東陽      1.205148e+07      6.245138e+06      2.445288e+07   
43    1321       大洋      2.447215e+06      1.190142e+06      4.467046e+06   
44    1323       永裕      1.809540e+06      8.253020e+05      3.241637e+06   
45    1324     地球工業      5.675900e+05      2.610600e+05      1.227153e+06   
46    1325       恒大      4.471370e+05      2.291240e+05      8.652100e+05   
47    1326       台化      1.986535e+08      9.895655e+07      3.584215e+08   
48    1337    再生-KY      7.167710e+05      3.438070e+05      4.588271e+06   
49    1338    廣華-KY      4.036378e+06      1.987165e+06      7.967359e+06   
50    1339       昭輝      1.431877e+06      7.228100e+05      2.837280e+06   
51

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = 107
season = 2
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_revenue.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_Revenue.xlsx', 'Revenue_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
